# Issues
- there are 57 missing cities -> so can't reference a state at all -> search through state for cities of nearest latitude and longitude to the accident
- accidents with streets that are missing -> Get rid of these????
- there are 9549 Accidents that don't have Airport_Code values. When merging df_acc (accidents) and df_air (airports), there are about 217,000 accidents that do not have matches in Airport dataset
    -  Solution???: search for city corresponding to airport, if not present, then search through airports in state with closest latitude and longitude
- How to deal with NaN values for Environment:
    - Precipitation - set to 0
    - Visibility - impute
    - Temperature - values of the next value for the same state after
    - Humidity - value of the next value for the same state after
    - Weather_Condition - set to clear
        - Transform stuff like scattered clouds, mostly cloudy, into one term (i.e. cloudy) for ease
    - Light_or_Darkness - check time of day before 7
    - Pressure - impute
    - Wind_Speed - value of the next value for the same state after
    - Wind_Direction - if precipitation is equal to 0 then clear...else, value of the next value for the same state after
- 

In [155]:
import pandas as pd
import numpy as np

import math

# datascraping for state - state code mapper
import requests # for datascrape
from bs4 import BeautifulSoup # datascrape

# distance calculation
import geopy.distance

# to time code
from timeit import default_timer as timer
import sys

# data imputation with MissForest
import sklearn.neighbors._base
sys.modules['sklearn.neighbors.base'] = sklearn.neighbors._base
from missingpy import MissForest # data imputation

# check if file exists
from pathlib import Path

In [158]:
# Load accident dataset
accident_data_path = '/Users/jonathanwozny/Documents/GraduateSchool/Fall2022/COP5725/Project/US_Accidents_Dec21_updated.csv'
df_acc = pd.read_csv(accident_data_path)

# Load Airport dataset
airport_data_path = '/Users/jonathanwozny/Documents/GraduateSchool/Fall2022/COP5725/Project/us-airports.csv'
df_air = pd.read_csv(airport_data_path)


In [159]:
pd.set_option('display.max_columns', None)

In [ ]:
pd.set_option('display.max_rows', None)
print(df_air.isna().sum())
pd.set_option('display.max_rows', 10)

In [160]:
pd.set_option('display.max_rows', None)
print(df_acc.isna().sum())
pd.set_option('display.max_rows', 10)

ID                             0
Severity                       0
Start_Time                     0
End_Time                       0
Start_Lat                      0
Start_Lng                      0
End_Lat                        0
End_Lng                        0
Distance(mi)                   0
Description                    0
Number                   1743911
Street                         2
Side                           0
City                         137
County                         0
State                          0
Zipcode                     1319
Country                        0
Timezone                    3659
Airport_Code                9549
Weather_Timestamp          50736
Temperature(F)             69274
Wind_Chill(F)             469643
Humidity(%)                73092
Pressure(in)               59200
Visibility(mi)             70546
Wind_Direction             73775
Wind_Speed(mph)           157944
Precipitation(in)         549458
Weather_Condition          70636
Amenity   

In [161]:
df_air.loc[df_air['gps_code'].isna(), 'gps_code'] = df_air.loc[df_air['gps_code'].isna(), 'ident']

In [162]:
# combine datasets - this is useful for when city names don't match exactly...can just choose one... 
#    i.e. St Louis != St. Louis
df = df_acc.merge(df_air, left_on=['Airport_Code'], right_on = ['ident'], how='left')

In [163]:
# Environment(Env_ID : integer, Precipitation : decimal, Visibility : integer, 
#             Temperature : decimal, Humidity : decimal, weather_condition : string, 
#             Light_Or_Darkness : boolean, Air_pressure : decimal, Wind_Speed : decimal, Wind_Direction : string) 

keep_cols = ['ID', 'Severity', 'Start_Time', 'Start_Lat', 'Start_Lng', 'Distance(mi)', 'Street',
       'Side', 'City', 'County', 'State', 'Zipcode', 'Country', 'Timezone',
       'Airport_Code', 'Temperature(F)',
       'Humidity(%)', 'Pressure(in)', 'Visibility(mi)', 'Wind_Direction',
       'Wind_Speed(mph)', 'Precipitation(in)', 'Weather_Condition', 'Amenity',
       'Bump', 'Crossing', 'Give_Way', 'Junction', 'No_Exit', 'Railway',
       'Roundabout', 'Station', 'Stop', 'Traffic_Calming', 'Traffic_Signal',
       'Turning_Loop', 'Sunrise_Sunset', 'ident', 'type', 'name', 'latitude_deg',
       'longitude_deg', 'region_name',  'local_region',
       'municipality', 'gps_code']
df = df[keep_cols]

In [164]:
df.loc[df["City"].isna(), "City"] = df.loc[df["City"].isna(), "municipality"]

In [165]:
pd.set_option('display.max_rows', 10)
df

ID  Severity           Start_Time  Start_Lat   Start_Lng  \
0              A-1         3  2016-02-08 00:37:08  40.108910  -83.092860   
1              A-2         2  2016-02-08 05:56:20  39.865420  -84.062800   
2              A-3         2  2016-02-08 06:15:39  39.102660  -84.524680   
3              A-4         2  2016-02-08 06:51:45  41.062130  -81.537840   
4              A-5         3  2016-02-08 07:53:43  39.172393  -84.492792   
...            ...       ...                  ...        ...         ...   
2845337  A-2845338         2  2019-08-23 18:03:25  34.002480 -117.379360   
2845338  A-2845339         2  2019-08-23 19:11:30  32.766960 -117.148060   
2845339  A-2845340         2  2019-08-23 19:00:21  33.775450 -117.847790   
2845340  A-2845341         2  2019-08-23 19:00:21  33.992460 -118.403020   
2845341  A-2845342         2  2019-08-23 18:52:06  34.133930 -117.230920   

         Distance(mi)            Street Side         City          County  \
0               3.230       Outerbelt E    R       Dublin        Franklin   
1               0.747            I-70 E    R       Dayton      Montgomery   
2               0.055            I-75 S    R   Cincinnati        Hamilton   
3               0.123            I-77 N    R        Akron          Summit   
4               0.500            I-75 S    R   Cincinnati        Hamilton   
...               ...               ...  ...          ...             ...   
2845337         0.543      Pomona Fwy E    R    Riverside       Riverside   
2845338         0.338             I-8 W    R    San Diego       San Diego   
2845339         0.561  Garden Grove Fwy    R       Orange          Orange   
2845340         0.772   San Diego Fwy S    R  Culver City     Los Angeles   
2845341         0.537          CA-210 W    R     Highland  San Bernardino   

        State Zipcode Country    Timezone Airport_Code  Temperature(F)  \
0          OH   43017      US  US/Eastern         KOSU            42.1   
1          OH   45424      US  US/Eastern         KFFO            36.9   
2          OH   45203      US  US/Eastern         KLUK            36.0   
3          OH   44311      US  US/Eastern         KAKR            39.0   
4          OH   45217      US  US/Eastern         KLUK            37.0   
...       ...     ...     ...         ...          ...             ...   
2845337    CA   92501      US  US/Pacific         KRAL            86.0   
2845338    CA   92108      US  US/Pacific         KMYF            70.0   
2845339    CA   92866      US  US/Pacific         KSNA            73.0   
2845340    CA   90230      US  US/Pacific         KSMO            71.0   
2845341    CA   92346      US  US/Pacific         KSBD            79.0   

         Humidity(%)  Pressure(in)  Visibility(mi) Wind_Direction  \
0               58.0         29.76            10.0             SW   
1               91.0         29.68            10.0           Calm   
2               97.0         29.70            10.0           Calm   
3               55.0         29.65            10.0           Calm   
4               93.0         29.69            10.0            WSW   
...              ...           ...             ...            ...   
2845337         40.0         28.92            10.0              W   
2845338         73.0         29.39            10.0             SW   
2845339         64.0         29.74            10.0            SSW   
2845340         81.0         29.62            10.0             SW   
2845341         47.0         28.63             7.0             SW   

         Wind_Speed(mph)  Precipitation(in) Weather_Condition  Amenity   Bump  \
0                   10.4               0.00        Light Rain    False  False   
1                    NaN               0.02        Light Rain    False  False   
2                    NaN               0.02          Overcast    False  False   
3                    NaN                NaN          Overcast    False  False   
4                   10.4               0.01        Ligh

# Handle NaN Values

In [166]:
pd.set_option('display.max_rows', None)
print(df.isna().sum())
pd.set_option('display.max_rows', 10)

ID                        0
Severity                  0
Start_Time                0
Start_Lat                 0
Start_Lng                 0
Distance(mi)              0
Street                    2
Side                      0
City                     56
County                    0
State                     0
Zipcode                1319
Country                   0
Timezone               3659
Airport_Code           9549
Temperature(F)        69274
Humidity(%)           73092
Pressure(in)          59200
Visibility(mi)        70546
Wind_Direction        73775
Wind_Speed(mph)      157944
Precipitation(in)    549458
Weather_Condition     70636
Amenity                   0
Bump                      0
Crossing                  0
Give_Way                  0
Junction                  0
No_Exit                   0
Railway                   0
Roundabout                0
Station                   0
Stop                      0
Traffic_Calming           0
Traffic_Signal            0
Turning_Loop        

## Fill Missing Airport Values (after merging Accident and Airport dataset)

In [167]:
air_cols_toRet = ['type', 'name', 'latitude_deg',
       'longitude_deg', 'region_name',  'local_region',
       'municipality']

In [180]:
# remove NaN values to make function work
df = df[df['City'].notna()]
df.reset_index(inplace=True)
df.drop('index', axis = 1, inplace=True)


df_air = df_air[df_air['municipality'].notna()]
df_air.reset_index(inplace=True)
df_air.drop('index', axis = 1, inplace=True)

# check that values are dropped
print(df['City'].isna().sum())
print(df_air['municipality'].isna().sum())

0
0


#### For each row of the dataframe (using apply and lambda function), this function finds the nearest airport to the accident based on the latitude and longitude coordinates

In [181]:
# speed up to use with apply and lambda function for dataframe
# ASSUMES NO NAN VALUES FOR City, State, Municipality, local_region, Start_Lat, Start_Lng, latitude_deg, longitude_deg
def NearestAirportSearchDF(dfRow, air_cols = air_cols_toRet, df_air=df_air):
    start = timer()
    closest_index = 'None'
    closest_ind = -1
    closest_dist = float(sys.maxsize)
    coords_1 = [dfRow['Start_Lat'], dfRow['Start_Lng']]
    retList = []
    # search to find city first, and if not, search through state
    temp_df = df_air.loc[(df_air['local_region'] == dfRow['State']) & (dfRow['City'] == df_air['municipality'])]
    if (len(temp_df.index)):
        for index, row in temp_df.iterrows():
            coords_2 = [row['latitude_deg'], row['longitude_deg']]
            dist = geopy.distance.geodesic(coords_1, coords_2).mi
            if (dist < closest_dist):
                closest_ind = index
                closest_index = row['ident']
                closest_dist = dist
    else:
        for index, row in df_air.loc[df_air['local_region'] == dfRow['State']].iterrows():
            coords_2 = [row['latitude_deg'], row['longitude_deg']]
            dist = geopy.distance.geodesic(coords_1, coords_2).mi
            if (dist < closest_dist):
                closest_ind = index
                closest_index = row['ident']
                closest_dist = dist
    dfRow['ident'] = closest_index
    dfRow['Nearest_Air_Dist'] = closest_dist
    dfRow[air_cols_toRet] = df_air.iloc[closest_ind][air_cols_toRet]
    end = timer()
    print(end-start)
    return dfRow

In [215]:
# check if the file already exists because it may take long depending on how many values
my_file = Path("Acc_Air_Merge.csv")

if not my_file.is_file():
    ### NOTE: THIS WILL TAKE ABOUT 7-8 HOURS FOR THE ACCIDENT DATASET
    df['Nearest_Air_Dist'] = 0
    df.loc[df['ident'].isna()] = df.loc[df['ident'].isna()].apply(lambda x: NearestAirportSearchDF(x), axis=1)
    df.to_csv('Acc_Air_Merge.csv')
else:
    df = pd.read_csv(my_file)

In [216]:
# confirm no null values for desired airport columns
print(df[['ident'] + air_cols_toRet].isna().sum())

ident            0
type             0
name             0
latitude_deg     0
longitude_deg    0
region_name      0
local_region     0
municipality     0
dtype: int64


#### This Function Calculates the Nearest Distance to the Airport, Given Nearest Airport Already Found
##### Basically the above function to find the nearest airport, did not record some of the distances (might might have been because Nearest_Air_Dist wasn't created outside of the function

In [400]:
copy_df = df.copy()

In [405]:
copy_df['Start_Lat']

0          40.108910
1          39.865420
2          39.102660
3          41.062130
4          39.172393
             ...    
2845279    34.002480
2845280    32.766960
2845281    33.775450
2845282    33.992460
2845283    34.133930
Name: Start_Lat, Length: 2845284, dtype: float64

In [423]:
def NearestAirDistCalc(row):
    coords_1 = (row['Start_Lat'], row['Start_Lng'])
    coords_2 = (row['latitude_deg'], row['longitude_deg'])
    dist = geopy.distance.geodesic(coords_1, coords_2).mi
    row['Nearest_Air_Dist'] = dist
    return row

In [440]:
if (df['Nearest_Air_Dist'].iloc[0] == 0):
    df = df.apply(lambda x: NearestAirDistCalc(x), axis=1)

## Environment NaN's
- How to deal with NaN values for Environment:
    - Precipitation     - set to 0
    - Visibility        - impute
    - Temperature       - Average of City, State or Average of State if City,State does not exist
    - Humidity          - Average of City, State or Average of State if City,State does not exist
    - Pressure          - Average of City, State or Average of State if City,State does not exist
    - Weather_Condition - if precipitation is equal to 0 then clear...else, value of the next value for the same state 
    - Light_or_Darkness - check time of day before 7 pm and after 6 am is light
    - Wind_Speed        - value of the next value for the same state after, set rest of values to 0
    - Wind_Direction    - if wind_speed is equal to 0 or NaN then calm...else set rest of values to calm

#### This function finds the average value for the corresponding city, state (or just state) combination for the desired column(s)

In [217]:
def AverageOfCityState(val, col, cs_avg, s_avg):
    # if it is nan, then do state groupby, otherwise do citystate groupby to get avg
    if (math.isnan(float(cs_avg.loc[val['City']].loc[val['State']][col]))):
        val[col] = s_avg.loc[val['State']][col]
    else:
        val[col] = cs_avg.loc[val['City']].loc[val['State']][col]
    
    return val

#### This function fills the cols with the strategy/function above

In [218]:
def FillWithCityStateAvg(data, fill_cols):
    print("FillWithCityStateAvg")
    
    cityStateCols = ['City', 'State']
    # groupby dataframes
    citystate_avg = data[cityStateCols + fill_cols].groupby(cityStateCols).mean()
    state_avg = data[['State'] + fill_cols].groupby('State').mean()

    # fill the columns with averages of city and state or average of just state
    for col in fill_cols:
        data.loc[data[col].isna(), cityStateCols + [col]] = data.loc[data[col].isna(), cityStateCols + [col]].apply(lambda x: AverageOfCityState(x, col, citystate_avg, state_avg), axis = 1)
    
    return data[fill_cols]
        

#### This function imputes values for given column(s) using given reference columns

In [219]:
def ImputeValues(data, imp_col, ref_cols, make_cat = True):
    print("Impute Values")
    
    # setup for imputation
    fakeFill = 9999999
    data[imp_col].fillna(fakeFill, inplace=True)
    temp_imp = data[[imp_col] + ref_cols]
    
    # encode non-integer values
    for col in temp_imp.columns:
        if (temp_imp[col].dtype == 'O'):
            # put all unique values into list
            myList = temp_imp[col].unique()
            # dictionary to map values to encoded integers by index
            mapper = dict(map(reversed,enumerate(myList))) 
            # map to encoded values
            temp_imp[col] = temp_imp[col].apply(lambda x: mapper[x])
    
    # impute with MissForest
    imputer = MissForest(missing_values = fakeFill, criterion=('squared_error', 'gini')) # instantiate and replace set value
    X_imputed = imputer.fit_transform(temp_imp)
    X_imputedDF = pd.DataFrame(X_imputed, columns = [imp_col] + ref_cols)
    if make_cat:
        X_imputedDF[imp_col] = X_imputedDF[imp_col].apply(lambda x: round(x))

    return X_imputedDF[imp_col]


#### This function fills all the Environment columns based on the strategy in the higher level header above

In [398]:
def FillEnvironmentNaN(data):
    # Precipitation
    data['Precipitation(in)'].fillna(0, inplace=True)
    
    # Light_or_Darkness
    data['Light_Or_Darkness'] = data['Start_Time'].apply(lambda x: 'Day' if (int(x[11:13]) < 19  and int(x[11:13]) > 6) else 'Night')
    
    # Weather_Condition - if precipitation is equal to 0 then clear...if equal to value, then set to rain
    # re-encode to 4 categories
    data.loc[(data['Weather_Condition'].isna()) & (data['Precipitation(in)'] == 0), 'Weather_Condition'] = 'Clear'
    data.loc[(data['Weather_Condition'].isna()) & (data['Precipitation(in)'] != 0), 'Weather_Condition'] = 'Rain'
    
    new_wcond = {'Snow' : ['Snow', 'Ice', 'Hail', 'Wintry', 'Sleet'], 
             'Clear' : ['Overcast', 'Cloudy', 'Clear', 'Fair', 'Scattered Clouds'], 
             'Rain' : ['Rain', 'Drizzle', 'Showers', 'Thunder', 'T-Storm', 'Showers', 'Precipitation'], 
             'Not_Clear': ['Fog', 'Smoke', 'Sand', 'Mist', 'Dust', 'Haze','Squalls', 'Funnel', 'Tornado', 'Volcanic Ash']}
    for key in new_wcond:
        df.loc[df['Weather_Condition'].str.contains('|'.join(new_wcond[key])) == True, 'Weather_Condition'] = key
    
    # Wind_Speed - if Wind_Direction has value, but Wind_Speed is NaN, set to 0 - now it has about the same amount of NaN's as Wind_Direction
    data.loc[(df_acc['Wind_Speed(mph)'].isna()) & (data['Wind_Direction'].notna()), 'Wind_Speed(mph)'] = 0
    
    # Wind_Direction - if Wind_Speed is Nan, then calm
    data.loc[(data['Wind_Speed(mph)'].isna()) & (data['Wind_Direction'].notna()), 'Wind_Direction'] = 'Calm'
    
    # Leftover Wind_Speed and Wind_Direction will be set to calm and 0
    data[['Wind_Speed(mph)', 'Wind_Direction']] = [0, 'Calm']
    
    # Fill values with averages of the corresponding city and state or the corresponding state
    avg_fill_cols = ['Temperature(F)', 'Humidity(%)', 'Pressure(in)']
    data[avg_fill_cols] = FillWithCityStateAvg(data, avg_fill_cols)
    
    
    # Impute Visibility
    imp_col = 'Visibility(mi)'
    ref_cols = ['Precipitation(in)', 'Wind_Speed(mph)', 'Weather_Condition']
    data[imp_col] = ImputeValues(data, imp_col, ref_cols)
    data.loc[data[imp_col] > 10, imp_col] = 10
    
    return data


In [221]:
# handle environment NaN's
# columns that cannot have null values
    # City, State
df = FillEnvironmentNaN(df)

FillWithCityStateAvg
Impute Values


<ipython-input-219-718cdbb4230a>:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  temp_imp[col] = temp_imp[col].apply(lambda x: mapper[x])


Iteration: 0
Iteration: 1
Iteration: 2
Iteration: 3
Iteration: 4
Iteration: 5


In [226]:
df.drop('Unnamed: 0', inplace=True, axis=1)

In [227]:
pd.set_option('display.max_rows', None)
print(df.isna().sum())
pd.set_option('display.max_rows', 10)

ID                        0
Severity                  0
Start_Time                0
Start_Lat                 0
Start_Lng                 0
Distance(mi)              0
Street                    0
Side                      0
City                      0
County                    0
State                     0
Zipcode                1318
Country                   0
Timezone               3658
Airport_Code           9548
Temperature(F)            0
Humidity(%)               0
Pressure(in)              0
Visibility(mi)            0
Wind_Direction            0
Wind_Speed(mph)           0
Precipitation(in)         0
Weather_Condition         0
Amenity                   0
Bump                      0
Crossing                  0
Give_Way                  0
Junction                  0
No_Exit                   0
Railway                   0
Roundabout                0
Station                   0
Stop                      0
Traffic_Calming           0
Traffic_Signal            0
Turning_Loop        

## Road NaNs
- Remove the rows with 2 streets
- Fill zipcode values with zipcode of nearest accident to it

In [223]:
# remove the 2 streets
df = df[df['Street'].notna()]
df.reset_index(inplace=True)
df.drop('index', axis = 1, inplace=True)

#### This function returns a zipcode for the matching city and state, otherwise returns the most occuring in the state
#### It assumes that City, State, Start_Lat, Start_Lng
#### This has high complexity

In [425]:
def FillNearestZipcode(row, col, data):
    closest_zip = 'None'
    closest_ind = -1
    closest_dist = float(sys.maxsize)
    coords_1 = [row['Start_Lat'], row['Start_Lng']]
    
    # search to find nearest accident in the same city
    temp_df = data.loc[(data['State'] == row['State']) & (data['City'] == row['City'])]
    
    if (len(temp_df.index)): # if not empty
        for index, r in temp_df.iterrows():
            coords_2 = [r['Start_Lat'], r['Start_Lng']]
            dist = geopy.distance.geodesic(coords_1, coords_2).mi
            if (dist < closest_dist):
                closest_ind = index
                closest_zip = r[col]
                closest_dist = dist
    
    else: # if empty
        for index, r in data.loc[data['State'] == row['State']].iterrows():
            if index > 10:
                break
            coords_2 = [r['Start_Lat'], r['Start_Lng']]
            dist = geopy.distance.geodesic(coords_1, coords_2).mi
            if (dist < closest_dist):
                closest_ind = index
                closest_zip = r[col]
                closest_dist = dist
    
    row[col] = closest_zip
    return row
    

In [311]:
# fill the nan values for zipcode
notna_zip_df = df.loc[df['Zipcode'].notna(), ['Start_Lat', 'Start_Lng', 'City', 'State', 'Zipcode']]
df.loc[df['Zipcode'].isna()] = df.loc[df['Zipcode'].isna()].apply(lambda x: FillNearestZipcode(x, 'Zipcode', notna_zip_df), axis=1)
# get rid of second dash in zipcode
df['Zipcode'] = df['Zipcode'].str[:5]

1.1378342889984197
0.48918164600036107
0.45732686200062744
0.4048909539997112
1.291773691002163
0.4368092250006157
1.0156812179993722
0.9008789639992756
0.8023106389991881
0.4526630489999661
0.912899462000496
0.7637813799992728
0.3745775909992517
0.5866453899980115
0.3809297659972799
0.3779772750021948
0.6975665989994013
0.8038214600019273
0.7427654940001958
0.6963222039994434
0.5550908690020151
0.7222028989999671
0.8993056180006533
0.9380483050008479
0.5733950700014248
0.4112606969974877
0.4301857639984519
0.7827584100014064
0.37532489700242877
0.45163776600020356
0.8009454809980525
0.7318924409992178
0.639719745999173
0.6616846949982573
0.8571912480001629
0.7109211730021343
0.645399916000315
0.3752491729974281
0.6592637249996187
0.33487922299900674
0.6163947080021899
0.33491750200118986
0.33629471600215766
0.5413684619998094
0.7804425739996077
0.4170408470017719
0.6451222010000492
0.6767075329989893
0.699810289999732
0.6936124179992476
0.6055554180020408
0.7365082049982448
0.60986077

0.7927947969983506
0.3655865779983287
0.6128610310006479
0.5362702250022267
0.7135480459983228
0.6036848740004643
0.6398295539984247
0.3583684990007896
0.35916376399836736
0.37628401899928576
0.5515299519975088
0.3511758299973735
0.6312828299996909
0.3498430079998798
0.5582530110004882
0.353690487001586
0.565912797999772
0.6417763399986143
0.708338188000198
0.6971638809991418
0.44027132599876495
0.7310049529987737
0.5557793420011876
0.6492562140010705
0.6162115240003914
0.4188674200013338
0.5822598129998369
0.643091566998919
0.6205424869986018
0.4049239480009419
0.4186341690001427
0.40988150499833864
0.8552369579992956
0.7222542489980697
0.7121498939995945
0.6979504100017948
0.4617870629990648
0.40659921300175483
0.3516727720016206
0.6297555540004396
0.7729574680015503
0.7512429879971023
0.3548457930010045
0.38571443599721533
0.5543273110015434
0.5479101159980928
0.337226820000069
0.3743508989973634
0.6169180830002006
0.7444816789975448
0.5363858380005695
0.35261431700200774
0.35294059

0.8011465149975265
0.6066723129988532
0.3415692950002267
0.6754995379997126
0.41564468599972315
0.8536978640004236
0.34781959999963874
0.8463444779990823
0.7051784739996947
0.7267979319985898
0.8329757469982724
0.7828500729992811
0.4411433780005609
0.8366700459991989
0.9203980410020449
0.37280756299878703
0.8543779800020275
0.7873956959992938
0.6825967190015945
0.7188484860016615
1.5916933529988455
1.48136903699924
1.4785164809982234
0.7787222400002065
0.787113843998668
0.7828884200025641
0.6754057459984324
0.7855083260001265
0.6986184749985114
0.35919448000277043
0.6326263650007604
0.6218891640019137
2.0964272349992825
0.5891207639979257
0.683280201999878
0.5997985869980766
0.3823279680000269
0.6206888470005651
0.6863301230005163
0.8355673160003789
1.4842573510031798
0.7030629769978987
0.4035608300000604
0.516648703996907
0.9726688119990285
0.6935971739985689
0.4153053390000423
0.37333519300227636
0.7458098110000719
0.7675220919991261
0.7386664719997498
0.3868546449994028
0.7521015550

0.42455137299839407
0.6374329330028559
0.607422166998731
0.5685465399983514
0.5480716910024057
0.5291798809994361
0.5294597780011827
0.6556283390018507
0.6957987309979217
0.5593241329988814
0.6020623100012017
0.5661736040019605
0.5566335000003164
0.5459170340000128
0.7354414870023902
0.5810504779983603
0.6590787599998293
0.6197319610000704
0.5441582260027644
1.2561923659995955
0.5278139990005002
0.5262475319977966
0.36771783899894217
0.37208806200214894
0.5462130480009364


In [312]:
df.Zipcode.isna().sum()

0

# Old Stuff

### Weather Condition - Add to Environment Function

In [315]:
new_wcond = {'Snow' : ['Snow', 'Ice', 'Hail', 'Wintry', 'Sleet'], 
             'Clear' : ['Overcast', 'Cloudy', 'Clear', 'Fair', 'Scattered Clouds'], 
             'Rain' : ['Rain', 'Drizzle', 'Showers', 'Thunder', 'T-Storm', 'Showers', 'Precipitation'], 
             'Not_Clear': ['Fog', 'Smoke', 'Sand', 'Mist', 'Dust', 'Haze','Squalls', 'Funnel', 'Tornado', 'Volcanic Ash']}

In [397]:
for key in new_wcond:
    df.loc[df['Weather_Condition'].str.contains('|'.join(new_wcond[key])) == True, 'Weather_Condition'] = key
print(df['Weather_Condition'].value_counts())

Clear        2464811
Rain          221876
Not_Clear      89498
Snow           57957
10             11142
Name: Weather_Condition, dtype: int64


In [ ]:
Snow -> Keywords: 'Snow', 'Ice', 'Hail', 'Wintry', 'Sleet'
#'Snow', 
#'Light Snow',
#'Blowing Snow',
#'Heavy Snow', 
#'Snow Grains',
#'Light Ice Pellets', 
#'Heavy Thunderstorms and Snow', 
#'Light Snow Showers',
#'Ice Pellets', 
#'Light Thunderstorms and Snow', 
#'Wintry Mix'
#'Wintry Mix / Windy',
#'Light Snow / Windy', 
#'Heavy Ice Pellets', 
#'Heavy Snow / Windy',
#'Snow / Windy', 
#'Light Snow and Sleet', 
#'Light Snow Shower', 
#'Snow and Sleet',
#'Light Snow with Thunder', 
#'Blowing Snow / Windy', 
#'Snow and Thunder / Windy',
#'Thunder / Wintry Mix',
#'Blowing Snow Nearby', 
#'Hail',
#'Light Snow and Sleet / Windy', 
#'Thunder and Hail',
#'Snow and Sleet / Windy',
#'Drifting Snow', 
#'Heavy Blowing Snow',
#'Low Drifting Snow', 
#'Light Blowing Snow', 
#'Heavy Thunderstorms with Small Hail',
#'Heavy Snow with Thunder', 
#'Thunder and Hail / Windy'
#'Thunder / Wintry Mix / Windy',
#'Small Hail', 
#'Light Sleet', 
#'Heavy Sleet',
#'Sleet',
#'Sleet / Windy',
#'Light Sleet / Windy',


Non-Precipitous -> Keywords: 'Overcast', 'Cloudy', 'Clear', 'Fair', 'Scattered Clouds'
# 'Overcast', 
# 'Mostly Cloudy', 
# 'Cloudy', 
# 'Scattered Clouds', 
# 'Clear', 
# 'Partly Cloudy',
# 'Fair', 
# 'Fair / Windy', 
# 'Cloudy / Windy',
# 'Partly Cloudy / Windy',
# 'Mostly Cloudy / Windy',

Not Clear -> Keywords: 'Fog', 'Smoke', 'Sand', 'Mist', 'Dust', 'Haze','Squalls', 'Funnel', 'Tornado', 'Volcanic Ash'
# 'Fog', 
# 'Patches of Fog', 
# 'Mist',
# 'Smoke',
# 'Light Freezing Fog', 
# 'Light Fog', 
# 'Shallow Fog', 
# 'Sand',
# 'Widespread Dust', 
# 'Blowing Dust / Windy', 
# 'Blowing Dust', 
# 'Volcanic Ash',
# 'Fog / Windy',
# 'Dust Whirls', 
# 'Haze / Windy',
# 'Sand / Dust Whirlwinds',
# 'Smoke / Windy',
# 'Widespread Dust / Windy',
# 'Partial Fog', 
# 'Sand / Windy',
# 'Duststorm',
# 'Sand / Dust Whirlwinds / Windy', 
# 'Sand / Dust Whirls Nearby',
# 'Tornado', 
# 'Squalls / Windy', 
# 'Blowing Sand',
# 'Mist / Windy', 
# 'Patches of Fog / Windy', 
# 'Light Haze', 
# 'Haze', 
# 'Funnel Cloud',
# 'Squalls', 

Rain -> Keywords: 'Rain', 'Drizzle', 'Showers', 'Thunder', 'T-Storm', 'Showers', 'Precipitation'
# 'Light Rain', 
# 'Light Freezing Drizzle', 
# 'Light Drizzle', 
# 'Heavy Rain',
# 'Drizzle',
# 'Thunderstorms and Rain',
# 'Rain', 
# 'Heavy Thunderstorms and Rain', 
# 'Thunderstorm',
# 'Thunder', 
# 'Thunder in the Vicinity',
# 'Light Rain with Thunder',
# 'N/A Precipitation',
# 'T-Storm', 
# 'Rain / Windy',
# 'Heavy T-Storm', 
# 'Light Rain / Windy'
# 'Freezing Rain / Windy', 
# 'Heavy Rain / Windy', 
# 'Heavy T-Storm / Windy', 
# 'Showers in the Vicinity', 
# 'Thunder / Windy', 
# 'Drizzle and Fog', 
# 'Drizzle / Windy',
# 'Light Rain Shower', 
# 'Rain Shower',
# 'T-Storm / Windy',
# 'Light Drizzle / Windy',
# 'Light Freezing Rain / Windy',
# 'Heavy Rain Shower / Windy',
# 'Light Rain Shower / Windy',
# 'Freezing Rain', 
# 'Freezing Drizzle',
# 'Heavy Freezing Rain',
# 'Heavy Rain Shower', 
# 'Heavy Rain Showers',
# 'Rain Showers', 
# 'Light Rain Showers',
# 'Heavy Drizzle', 
# 'Light Thunderstorms and Rain', 
# 'Heavy Freezing Drizzle', 

In [17]:
# Precipitation
df_acc['Precipitation(in)'].fillna(0, inplace=True)

In [18]:
# Light_or_Darkness
df_acc['Light_Or_Darkness'] = df_acc['Start_Time'].apply(lambda x: 'Day' if (int(x[11:13]) < 19  and int(x[11:13]) > 6) else 'Night')

In [144]:
# Load accident dataset
accident_data_path = '/Users/jonathanwozny/Documents/GraduateSchool/Fall2022/COP5725/Project/US_Accidents_Dec21_updated.csv'
df_acc = pd.read_csv(accident_data_path)

In [145]:
temp_acc = df_acc.copy()

In [153]:
temp_acc['Weather_Condition'].unique()

array(['Light Rain', 'Overcast', 'Mostly Cloudy', 'Snow', 'Light Snow',
       'Cloudy', 'Rain', 'Scattered Clouds', 'Clear', 'Partly Cloudy',
       'Light Freezing Drizzle', 'Light Drizzle', 'Haze', 'Heavy Rain',
       'Fair', 'Drizzle', 'Fog', 'Thunderstorms and Rain',
       'Patches of Fog', 'Light Thunderstorms and Rain', 'Mist',
       'Rain Showers', 'Light Rain Showers', 'Heavy Drizzle', 'Smoke',
       'Light Freezing Fog', 'Light Freezing Rain', 'Blowing Snow',
       'Heavy Thunderstorms and Rain', 'Heavy Snow', 'Snow Grains',
       'Squalls', 'Light Fog', 'Shallow Fog', 'Thunderstorm',
       'Light Ice Pellets', 'Thunder', 'Thunder in the Vicinity',
       'Fair / Windy', 'Light Rain with Thunder',
       'Heavy Thunderstorms and Snow', 'Light Snow Showers',
       'Cloudy / Windy', 'Ice Pellets', 'N/A Precipitation',
       'Light Thunderstorms and Snow', 'T-Storm', 'Rain / Windy',
       'Wintry Mix', 'Partly Cloudy / Windy', 'Heavy T-Storm', 'Sand',
       'Light Rai

In [150]:
temp_acc.loc[(temp_acc['Weather_Condition'].isna()) & (temp_acc['Precipitation(in)'] == 0)] = 'Clear'


In [152]:
temp_acc.loc[(temp_acc['Weather_Condition'].isna()) & (temp_acc['Precipitation(in)'] != 0), 'Weather_Condition'] = 'Rain'


In [140]:
# Weather_Condition - if precipitation is equal to 0 then clear
df_acc.loc[(df_acc['Weather_Condition'].isna()) & (df_acc['Precipitation(in)'] == 0), 'Weather_Condition'] = 'Clear'


In [137]:
df_acc['Weather_Condition'].unique()

array(['Clear', nan], dtype=object)

In [ ]:
df_acc.loc[(df_acc['Weather_Condition'].isna()) & (df_acc['Precipitation(in)'] != 0), 'Weather_Condition'] = 'Rain'


In [ ]:
df_acc.unique()

In [130]:
df_acc['Weather_Condition'].isna().sum()

0

In [20]:
# Wind_Speed - if Wind_Direction has value, but Wind_Speed is NaN, set to 0
df_acc.loc[(df_acc['Wind_Speed(mph)'].isna()) & (df_acc['Wind_Direction'].notna()), 'Wind_Speed(mph)'] = 0

# now it has about the same amount of NaN's as Wind_Direction

In [21]:
# Wind_Direction - if Wind_Speed is Nan, then calm
df_acc.loc[(df_acc['Wind_Speed(mph)'].isna()) & (df_acc['Wind_Direction'].notna()), 'Wind_Direction'] = 'Calm'

In [22]:
df_acc[['Wind_Speed(mph)', 'Wind_Direction']].isna().sum()

Wind_Speed(mph)    73745
Wind_Direction     73775
dtype: int64

In [23]:
# Leftover Wind_Speed and Wind_Direction will be set to calm and 0
df_acc[['Wind_Speed(mph)', 'Wind_Direction']] = [0, 'Calm']

In [24]:
df_acc[['Wind_Speed(mph)', 'Wind_Direction']].isna().sum()

Wind_Speed(mph)    0
Wind_Direction     0
dtype: int64

### Average of GroupBy City and State, else Average of GroupBy State
- Temperature
- Humidity
- Pressure

In [25]:
def AverageOfCityState(val, col, cs_avg, s_avg):
    # if it is nan, then do state groupby, otherwise do citystate groupby to get avg
    if (math.isnan(float(cs_avg.loc[val['City']].loc[val['State']][col]))):
        val[col] = s_avg.loc[val['State']][col]
    else:
        val[col] = cs_avg.loc[val['City']].loc[val['State']][col]
    
    return val

In [26]:
# remove NaN values from City to make function work
df_acc = df_acc[df_acc['City'].notna()]
df_acc.reset_index(inplace=True)
df_acc.drop('index', axis = 1, inplace=True)

/Users/jonathanwozny/opt/anaconda3/lib/python3.8/site-packages/pandas/core/frame.py:4308: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  return super().drop(


In [27]:
indToCheck = df_acc['Temperature(F)'].isna() | df_acc['Humidity(%)'].isna() | df_acc['Pressure(in)'].isna()

In [28]:
# groupby dataframes
citystate_avg = df_acc[['City', 'State', 'Temperature(F)', 'Humidity(%)', 'Pressure(in)']].groupby(['City', 'State']).mean()
state_avg = df_acc[['State', 'Temperature(F)', 'Humidity(%)', 'Pressure(in)']].groupby('State').mean()

env_fill_cols = ['Temperature(F)', 'Humidity(%)', 'Pressure(in)']
for col in env_fill_cols:
    df_acc.loc[df_acc[col].isna(), ['City', 'State', col]] = df_acc.loc[df_acc[col].isna(), ['City', 'State', col]].apply(lambda x: AverageOfCityState(x, col, citystate_avg, state_avg), axis = 1)

In [29]:
df_acc[env_fill_cols].isna().sum()

Temperature(F)    0
Humidity(%)       0
Pressure(in)      0
dtype: int64

### Impute with Certain Columns
- Visibility
    - Values that affect visibility:
        - Precipitation, Wind_Speed, and Weather_Condition

In [30]:
df_acc['Visibility(mi)'].value_counts()

10.0     2230169
7.0        79647
9.0        68814
8.0        55950
5.0        53927
          ...   
16.0           1
110.0          1
43.0           1
34.0           1
54.0           1
Name: Visibility(mi), Length: 76, dtype: int64

In [127]:
df_acc[df_acc['Weather_Condition'].isna()]

ID  Severity           Start_Time             End_Time  \
6317        A-6318         2  2016-04-08 07:08:44  2016-04-08 13:08:44   
17938      A-17939         2  2016-10-27 03:50:37  2016-10-27 10:54:59   
18896      A-18897         2  2016-11-08 05:05:50  2016-11-08 11:05:50   
31345      A-31346         2  2016-07-28 18:21:54  2016-07-29 00:21:54   
31678      A-31679         3  2016-11-30 19:18:15  2016-12-01 01:18:15   
...            ...       ...                  ...                  ...   
2823458  A-2823596         2  2019-07-08 07:59:38  2019-07-08 08:29:03   
2823468  A-2823606         2  2019-07-08 08:31:05  2019-07-08 09:00:36   
2823471  A-2823609         3  2019-07-08 09:01:06  2019-07-08 09:30:10   
2827709  A-2827847         3  2019-07-17 19:44:31  2019-07-17 20:11:29   
2834741  A-2834879         2  2019-08-01 15:20:35  2019-08-01 15:50:20   

         Start_Lat   Start_Lng    End_Lat     End_Lng  Distance(mi)  \
6317     32.705300 -116.359180  32.706620 -116.364350         0.314   
17938    44.730540  -93.283130  44.727770  -93.282640         0.193   
18896    29.285960  -98.395650  29.275330  -98.396140         0.735   
31345    32.677810  -97.120000  32.677830  -97.106790         0.768   
31678    39.408430  -76.666920  39.413680  -76.661270         0.472   
...            ...         ...        ...         ...           ...   
2823458  39.499320  -76.667890  39.491140  -76.666940         0.567   
2823468  39.263211  -76.567739  39.263923  -76.588528         1.113   
2823471  39.281240  -76.730090  39.279870  -76.727630         0.162   
2827709  39.271530  -76.653420  39.269215  -76.659601         0.367   
2834741  39.265630  -76.614790  39.269702  -76.615059         0.282   

                                               Description  Number  \
6317        At Crestwood Rd - Accident. Left lane blocked.     NaN   
17938               At Crystal Lake Rd/Exit 87 - Accident.     NaN   
18896         At Southton Rd/Donop Rd/Exit 130 - Accident.     NaN   
31345                   At Matlock Rd/Exit 450 - Accident.     NaN   
31678                    At I-83/MD-25/Exit 23 - Accident.     NaN   
...                                                    ...     ...   
2823458  At Shawan Rd/Exit 20 - Accident. Right lane bl...     NaN   
2823468           At I-95 (West) - Accident. Lane blocked.     NaN   
2823471  At Edmondson Ave/Exit 14 - Accident. Two lanes...     NaN   
2827709  At US-1-ALT/Caton Ave/Exit 50 - Accident. Left...     NaN   
2834741  Between I-95/McComas St and Olive St - Acciden...  2153.0   

                    Street Side                  City            County State  \
6317                 I-8 W    R             Boulevard         San Diego    CA   
17938               I-35 S    R            Burnsville            Dakota    MN   
18896               I-37 S    R           San Antonio             Bexar    TX   
31345               I-20 E    R             Arlington           Tarrant    TX   
31678              I-695 E    R  Lutherville Timonium  Baltimore County    MD   
...                    ...  ...                   ...               ...   ...   
2823458             I-83 S    R          Cockeysville  Baltimore County    MD   
2823468  Fort McHenry Tunl    R             Baltimore    Baltimore City    MD   
2823471            I-695 S    R           Catonsville  Baltimore County    MD   
2827709             I-95 S    R             Baltimore    Baltimore City    MD   
2834741       S Hanover St    L             Baltimore    Baltimore City    MD   

            Zipcode Country    Timezone Airport_Code    Weather_Timestamp  \
6317          91905      US  US/Pacific         KCZZ  2016-04-08 06:52:00   
17938         55306      US  US/Central         KLVN  2016-10-27 03:49:00   
18896         78223      US  US/Central         KSSF  2016-11-08 04:53:00   
31345         76017      US  US/Central         KGKY  2016-07-28 18:43:00   
31678         21093      US  US/Eastern         KDMH  2016-11-30 18:54:00  

In [31]:
imp_cols = ['Visibility(mi)', 'Precipitation(in)', 'Wind_Speed(mph)', 'Weather_Condition']
fakeFill = 9999999
df_acc['Visibility(mi)'].fillna(9999999, inplace=True)
temp_imp = df_acc[imp_cols]
temp_imp['Weather_Condition']

# put all unique values into list
myList = temp_imp['Weather_Condition'].unique()
# dictionary to map values to encoded integers by index
mapper = dict(map(reversed,enumerate(myList))) 
# map to encoded values
temp_imp['Weather_Condition'] = temp_imp['Weather_Condition'].apply(lambda x: mapper[x])


imputer = MissForest(missing_values = 9999999, criterion=('squared_error', 'gini')) # instantiate and replace set value
X_imputed = imputer.fit_transform(temp_imp)

<ipython-input-31-bc4ab9c39acd>:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  temp_imp['Weather_Condition'] = temp_imp['Weather_Condition'].apply(lambda x: mapper[x])


Iteration: 0
Iteration: 1
Iteration: 2


In [43]:
df_acc['Visibility(mi)'].isna().sum()

0

In [41]:
X_imputedDF = pd.DataFrame(X_imputed, columns = imp_cols)
X_imputedDF['Visibility(mi)'] = X_imputedDF['Visibility(mi)'].apply(lambda x: round(x))

In [44]:
X_imputedDF['Visibility(mi)'].value_counts()

10     2230193
9       138414
7        79871
8        56204
2        54932
        ...   
34           1
110          1
111          1
19           1
130          1
Name: Visibility(mi), Length: 44, dtype: int64

## Airport NaN's

In [274]:
air_cols_toRet = ['type', 'name', 'latitude_deg',
       'longitude_deg', 'region_name',  'local_region',
       'municipality', 'gps_code']

In [275]:
# assuming putting everything as inputs
def NearestAirportSearch(state, lat, long, air_cols, df_air=df_air):
    closest_index = 'None'
    closest_dist = sys.maxsize
    coords_1 = [lat, long]
    retList = []
    for index, row in df_air.loc[df_air['local_region'] == state].iterrows():
        coords_2 = [row['latitude_deg'], row['longitude_deg']]
        dist = geopy.distance.geodesic(coords_1, coords_2).mi
        if (dist < closest_dist):
            closest_index = row['ident']
            closest_dist = dist
            rowsFromAirDF = row[air_cols]
            retList = row[air_cols]
    return closest_index, closest_dist, retList
    

In [276]:
# create row for nearest distance to airport
df['Nearest_Air_Dist'] = 0

In [38]:
start = timer()
NearestAirportSearch(df.iloc[25]['State'], df.iloc[25]['Start_Lat'], df.iloc[25]['Start_Lng'], air_cols_toRet)
end = timer()

In [39]:
print(end - start)

0.44389808200003245


In [ ]:
# columns to put into merged df_acc and df_air
air_cols_toRet = ['type', 'name', 'latitude_deg',
       'longitude_deg', 'region_name',  'local_region',
       'municipality', 'gps_code']

ct = 0
for ind, rows in df[df['ident'].isna()].iterrows():
    ct = ct + 1
    retVal = NearestAirportSearch(rows['State'], rows['Start_Lat'], rows['Start_Lng'], air_cols_toRet, df_air)
    rows['ident'] = retVal[0]
    rows['Nearest_Air_Dist'] = retVal[1]
    rows[air_cols_toRet] = retVal[2]
    
    if (ct % 10 == 0):
        print(ct)

In [ ]:
# to speed this up, try to do an apply, change to df.loc[df['ident'].isna(), ['']]

In [277]:
# remove NaN values to make function work
df = df[df['City'].notna()]
df.reset_index(inplace=True)
df.drop('index', axis = 1, inplace=True)


df_air = df_air[df_air['municipality'].notna()]
df_air.reset_index(inplace=True)
df_air.drop('index', axis = 1, inplace=True)

In [43]:
# check that values are dropped
pd.set_option('display.max_rows', None)
df.isna().sum()

ID                        0
Severity                  0
Start_Time                0
Start_Lat                 0
Start_Lng                 0
Distance(mi)              0
Street                    2
Side                      0
City                      0
County                    0
State                     0
Zipcode                1319
Country                   0
Timezone               3659
Airport_Code           9549
Temperature(F)        69271
Humidity(%)           73089
Pressure(in)          59197
Visibility(mi)        70543
Wind_Direction        73774
Wind_Speed(mph)      157941
Precipitation(in)    549455
Weather_Condition     70633
Amenity                   0
Bump                      0
Crossing                  0
Give_Way                  0
Junction                  0
No_Exit                   0
Railway                   0
Roundabout                0
Station                   0
Stop                      0
Traffic_Calming           0
Traffic_Signal            0
Turning_Loop        

In [44]:
df_air.isna().sum()

id                       0
ident                    0
type                     0
name                     0
latitude_deg             0
longitude_deg            0
elevation_ft          1998
continent            29381
country_name             0
iso_country              0
region_name              0
iso_region               0
local_region             0
municipality             0
scheduled_service        0
gps_code              8824
iata_code            27475
local_code            7920
home_link            28422
wikipedia_link       27003
keywords             24428
score                    0
last_updated             0
dtype: int64

In [45]:
pd.set_option('display.max_rows', 10)

In [313]:
# speed up to use with apply and lambda function for dataframe
# ASSUMES NO NAN VALUES FOR CITY
def NearestAirportSearchDF(dfRow, air_cols = air_cols_toRet, df_air=df_air):
    start = timer()
    closest_index = 'None'
    closest_ind = -1
    closest_dist = float(sys.maxsize)
    coords_1 = [dfRow['Start_Lat'], dfRow['Start_Lng']]
    retList = []
    # search to find city first, and if not, search through state
    temp_df = df_air.loc[(df_air['local_region'] == dfRow['State']) & (dfRow['City'] == df_air['municipality'])]
    if (len(temp_df.index)):
        for index, row in temp_df.iterrows():
            coords_2 = [row['latitude_deg'], row['longitude_deg']]
            dist = geopy.distance.geodesic(coords_1, coords_2).mi
            if (dist < closest_dist):
                closest_ind = index
                closest_index = row['ident']
                closest_dist = dist
    else:
        for index, row in df_air.loc[df_air['local_region'] == dfRow['State']].iterrows():
            coords_2 = [row['latitude_deg'], row['longitude_deg']]
            dist = geopy.distance.geodesic(coords_1, coords_2).mi
            if (dist < closest_dist):
                closest_ind = index
                closest_index = row['ident']
                closest_dist = dist
    dfRow['ident'] = closest_index
    dfRow['Nearest_Air_Dist'] = closest_dist
    dfRow[air_cols_toRet] = df_air.iloc[closest_ind][air_cols_toRet]
    end = timer()
    print(end-start)
    return dfRow

In [314]:
air_cols_toRet = ['type', 'name', 'latitude_deg',
       'longitude_deg', 'region_name',  'local_region',
       'municipality']

In [315]:
### NOTE: THIS WILL TAKE ABOUT 7-8 HOURS FOR THE ACCIDENT DATASET
df.loc[df['ident'].isna()] = df.loc[df['ident'].isna()].apply(lambda x: NearestAirportSearchDF(x), axis=1)

0.017459878989029676
1.006172745997901
0.9255157210136531
0.008340453001437709
1.201833312996314
0.008318063002661802
0.007664092991035432
0.921323331000167
0.008374668002943508
0.007957538997288793
1.0035238179989392
0.007454727005097084
0.00808630499523133
0.9064758669992443
0.9054687870084308
0.9126422039989848
0.007799815997714177
0.009022002996061929
0.0071044090000214055
0.007970905004185624
0.009148782002739608
0.009249341004760936
0.9066394840046996
0.008192665001843125
0.007893104004324414
0.9140575700002955
0.9132150700024795
0.008062936991336755
0.9258680040074978
0.00801047398999799
0.916057523994823
0.08834854999440722
0.8940379650011891
0.007379052010946907
0.0891045009921072
0.009439066998311318
0.007259877005708404
0.08750346400483977
0.4975955529953353
0.10124823400110472
0.09764695000194479
0.12971998000284657
0.11125328399066348
0.11467823199927807
0.1509481419925578
0.108001601009164
0.11995133699383587
0.10569021900300868
0.10115161899011582
0.09234452599775977
0.0

0.08805798400135245
0.9042757239949424
0.8972400360071333
0.006520924012875184
0.08854216599138454
0.009542244995827787
0.08956486999522895
0.09718082699691877
0.0887655169935897
0.007470090000424534
0.8991136709955754
0.08968117000767961
0.08758606199990027
0.0933424009999726
0.09438502301054541
0.009058747004019096
0.08768864799640141
0.09755374299129471
0.08946651501173619
0.8926613249932416
0.09264958000858314
0.08884862999548204
0.0926992700115079
0.09187756398750935
0.0878608650091337
0.007630985986907035
0.005888744999538176
0.00851332199817989
0.007448506003129296
0.006584888993529603
0.1002451359963743
0.08898689699708484
0.08912916500412393
0.09655814401048701
0.0889252229972044
0.08993954399193171
0.09651463100453839
0.08818586099368986
0.09308430799865164
0.8920134090003558
0.09066956701281015
0.09017862600740045
0.09474424700601958
0.0927795149909798
0.08782672900997568
0.09459441900253296
0.0920855160075007
0.0069685490016127005
0.08865443099057302
0.09645373601233587
0.8

0.8902931049960898
0.09108041701256298
0.09035661100642756
0.09829240900580771
0.08954557499964722
0.08879928800160997
0.10094737699546386
0.0069921970134601
0.007630874999449588
0.006676649994915351
0.006741477991454303
0.011176822998095304
0.008468405008898117
0.08996988300350495
0.8993407969974214
0.09014875000866596
0.09073427300609183
0.009497441991697997
0.006445698003517464
0.9099808510072762
0.08919699500256684
0.006760278993169777
0.09092740499181673
0.09558557499258313
0.0938962630025344
0.08847878300002776
0.008767769002588466
0.09977107399026863
0.0889321389986435
0.0891888690093765
0.09752458799630404
0.09117927399347536
0.006802037998568267
0.007382039009826258
0.08808831300120801
0.10100265199434943
0.006816485998569988
0.007037749994196929
0.0064380120020359755
0.09077176899882033
0.09233094300725497
0.007096792993252166
0.0981953699956648
0.08867608199943788
0.006950600989512168
0.09110764900106005
0.09607001500262413
0.08859082699927967
0.09015283000189811
0.095877054

0.06037256099807564
0.024181123008020222
0.06273353500000667
0.02407043999119196
0.053539813990937546
0.05532410899468232
0.061262411007191986
0.21114263600611594
0.015026715002022684
0.06521307000366505
0.057087909008259885
0.2900240649905754
0.056053713997243904
0.05560525300097652
0.014813223999226466
0.05839691999426577
0.05465567200735677
0.030977520000305958
0.056367785000475124
0.062107831006869674
0.05928133199631702
0.06163096000091173
0.05550091101031285
0.05571607999445405
0.05645066799479537
0.055213383995578624
0.06431871899985708
0.05583284699241631
0.0558186400012346
0.011981597010162659
0.025159819997497834
0.21170980299939401
0.055679240002064034
0.009783896995941177
0.055723567988025025
0.05389848999038804
0.05520167600479908
0.21333932899869978
0.2134507860027952
0.20879340700048488
0.06030534199089743
0.057762966011068784
0.05582205699465703
0.055736413996783085
0.21332894200168084
0.055076204997021705
0.022244003994273953
0.023423478996846825
0.05408455499855336
0.

0.05579588700493332
0.007935779998661019
0.05934796298970468
0.20732794399373233
0.00905944399710279
0.011074030990130268
0.05840609798906371
0.05639594100648537
0.07601180000347085
0.06336156099860091
0.05945150999468751
0.029153329000109807
0.021681633006664924
0.05522104899864644
0.022756286009098403
0.05506653600605205
0.008410473994445056
0.06323037001129705
0.012142191000748426
0.009935944006429054
0.21002180100185797
0.024422581991530024
0.0584786580002401
0.025266402997658588
0.029676200007088482
0.053484985008253716
0.26080670999363065
0.25433729600626975
0.008347969996975735
0.06107971699384507
0.023833687009755522
0.055088414999772795
0.05412270099623129
0.05436845700023696
0.027450765992398374
0.02437901600205805
0.024705857009394094
0.054504889994859695
0.05298143898835406
0.05413481700816192
0.06330789500498213
0.02384510700358078
0.006460142991272733
0.05342902199481614
0.025043870002264157
0.21737054799450561
0.05561717299860902
0.0593213719985215
0.05520754300232511
0.

...

0.09038974999566562
0.09042222300195135
0.08821697700477671
0.09049116099777166
0.0062902920035412535
0.09034981299191713
0.08837710300576873
0.007722627007751726
0.11579157199594192
0.013376949005760252
0.11218528299650643
0.0062751170044066384
0.01348932100518141
0.013511021999875084
0.005920862007769756
0.0063219619914889336
0.00702269199246075
0.007770473006530665
0.20350525398680475
0.014911799007677473
0.006412193994037807
0.022661479000817053
0.05289030099811498
0.014601471004425548
0.052417041995795444
0.009787470000446774
0.008743754005990922
0.006162203004350886
0.16603740000573453
0.00830351900367532
0.00664267799584195
0.008528285005013458
0.00848593600676395
0.008061621003434993
0.007082878990331665
0.2371547970105894
0.2412289000058081
0.009420647998922504
0.008178603005944751
0.005948485995759256
0.23719426699972246
0.00744889400084503
0.006333919998724014
0.09536387199477758
0.08810582499427255
0.015436578993103467
0.09548314000130631
0.11090517199772876
0.0102635240036

0.237648698996054
0.007961765004438348
0.0076616950100287795
0.007712318008998409
0.008740329998545349
0.00781975599238649
0.010549195008934475
0.010605603994918056
0.008339327992871404
0.008336444006999955
0.24390620600024704
0.23459582398936618
0.010270136001054198
0.09046733099967241
0.006616603001020849
0.006952534997253679
0.010957949998555705
0.006294013990554959
0.01487030899443198
0.007513703007134609
0.01004209900565911
0.16586200598976575
0.1627893499971833
0.007251535003888421
0.008029734992305748
0.0077333359949989244
0.23755690999678336
0.23770867400162388
0.23562379500071984
0.011737182008801028
0.0069464429980143905
0.008021339002880268
0.006674157993984409
0.006635264988290146
0.23633914699894376
0.08749057500972413
0.11173231399152428
0.11347251400002278
0.11199668700282928
0.1158170419948874
0.17893304101016838
0.17613263899693266
0.01416414900450036
0.11168786299822386
0.11250363099679817
0.009677524009020999
0.0067328680015634745
0.01383017300395295
0.01345580100314

0.00751688500167802
0.006205189987667836
0.007838577992515638
0.21522829998866655
0.16495968399976846
0.00592469799448736
0.23863276200427208
0.006297675994574092
0.006240640999749303
0.006224151991773397
0.0061908430070616305
0.0064506469934713095
0.01056500500999391
0.010701003004214726
0.010203825993812643
0.007539725003880449
0.008241442003054544
0.00827489499351941
0.00812103200587444
0.27985653500945773
0.013745143995038234
0.008032345998799428
0.01084609900135547
0.007173924008384347
0.08859899100207258
0.006763917001080699
0.08889908099081367
0.09020680299727246
0.08751927698904183
0.007352140004513785
0.8864553500025067
0.006491819993243553
0.0876892649976071
0.0879523240000708
0.09289627999532968
0.09513531699485611
0.08819975300866645
0.09062058599374723
0.08854780599358492
0.8785594729997683
0.08836696200887673
0.007490539996069856
0.08768478500132915
0.09036955199553631
0.007112802006304264
0.1150503020035103
0.012203271995531395
0.22091400899807923
0.006922470012796111
0.

0.2418410170066636
0.0064784839923959225
0.010254102002363652
0.24602340000274125
0.23689350800123066
0.006066446003387682
0.008085532987024635
0.006968601999687962
0.006392062990926206
0.23826233399449848
0.011433583000325598
0.23708002299827058
0.2378105669922661
0.2354772360122297
0.008754412003327161
0.23621893700328656
0.23648350100847892
0.24228030699305236
0.011652829998638481
0.010828087994013913
0.007314292990486138
0.00732599500042852
0.08766886900411919
0.08816178800771013
0.09096943099575583
0.08790020500600804
0.8813896089995978
0.08844348600541707
0.11280308500863612
0.006767484010197222
0.009709650999866426
0.009887460008030757
0.23865184899477754
0.008432533009909093
0.006131290007033385
0.23398405300395098
0.23414559299999382
0.0077831160015193745
0.2423935629922198
0.006827089993748814
0.006664822998573072
0.008249853999586776
0.23553073800576385
0.008579740999266505
0.006153565991553478
0.23468065599445254
0.2447503430012148
0.23586935699859168
0.24121568800183013
0.

0.49156057499931194
0.5205481730081374
0.007390058992314152
0.05482381199544761
0.05305415399197955
0.05310927800019272
0.006695415999274701
0.021632917996612377
0.05399723199661821
0.05638635600917041
0.052818090000073425
0.0075892610038863495
0.007437051011947915
0.007939429007819854
0.008394113989197649
0.00584664499911014
0.006253190993447788
0.008891703997505829
0.008127687993692234
0.24544661400432233
0.23906883598829154
0.006888340998557396
0.006819474991061725
0.24672891400405206
0.007207460992503911
0.007713181999861263
0.006387954010278918
0.23545339300471824
0.010453472001245245
0.00869559399143327
0.006453248002799228
0.010289450001437217
0.0067544259945861995
0.9056041220028419
0.9046017380023841
0.007088651997037232
0.05201514399959706
0.006709744004183449
0.012454691008315422
0.022267733002081513
0.023714894996373914
1.3809844899951713
0.006934167991857976
0.053241300003719516
0.05328896200808231
0.05331847399065737
0.05984020100731868
0.006271338002989069
0.006871195000

In [316]:
df.to_csv('Acc_Air_Merge.csv')

In [317]:
pd.set_option('display.max_rows', None)
df.isna().sum()

ID                        0
Severity                  0
Start_Time                0
Start_Lat                 0
Start_Lng                 0
Distance(mi)              0
Street                    2
Side                      0
City                      0
County                    0
State                     0
Zipcode                1319
Country                   0
Timezone               3659
Airport_Code           9549
Temperature(F)        69271
Humidity(%)           73089
Pressure(in)          59197
Visibility(mi)        70543
Wind_Direction        73774
Wind_Speed(mph)      157941
Precipitation(in)         0
Weather_Condition     70633
Amenity                   0
Bump                      0
Crossing                  0
Give_Way                  0
Junction                  0
No_Exit                   0
Railway                   0
Roundabout                0
Station                   0
Stop                      0
Traffic_Calming           0
Traffic_Signal            0
Turning_Loop        

In [318]:
pd.set_option('display.max_rows', 10)


In [321]:
fake_df = pd.read_csv('Acc_Air_Merge.csv')

In [322]:
fake_df

Unnamed: 0         ID  Severity           Start_Time  Start_Lat  \
0                 0        A-1         3  2016-02-08 00:37:08  40.108910   
1                 1        A-2         2  2016-02-08 05:56:20  39.865420   
2                 2        A-3         2  2016-02-08 06:15:39  39.102660   
3                 3        A-4         2  2016-02-08 06:51:45  41.062130   
4                 4        A-5         3  2016-02-08 07:53:43  39.172393   
...             ...        ...       ...                  ...        ...   
2845281     2845281  A-2845338         2  2019-08-23 18:03:25  34.002480   
2845282     2845282  A-2845339         2  2019-08-23 19:11:30  32.766960   
2845283     2845283  A-2845340         2  2019-08-23 19:00:21  33.775450   
2845284     2845284  A-2845341         2  2019-08-23 19:00:21  33.992460   
2845285     2845285  A-2845342         2  2019-08-23 18:52:06  34.133930   

          Start_Lng  Distance(mi)            Street Side         City  \
0        -83.092860         3.230       Outerbelt E    R       Dublin   
1        -84.062800         0.747            I-70 E    R       Dayton   
2        -84.524680         0.055            I-75 S    R   Cincinnati   
3        -81.537840         0.123            I-77 N    R        Akron   
4        -84.492792         0.500            I-75 S    R   Cincinnati   
...             ...           ...               ...  ...          ...   
2845281 -117.379360         0.543      Pomona Fwy E    R    Riverside   
2845282 -117.148060         0.338             I-8 W    R    San Diego   
2845283 -117.847790         0.561  Garden Grove Fwy    R       Orange   
2845284 -118.403020         0.772   San Diego Fwy S    R  Culver City   
2845285 -117.230920         0.537          CA-210 W    R     Highland   

                 County State Zipcode Country    Timezone Airport_Code  \
0              Franklin    OH   43017      US  US/Eastern         KOSU   
1            Montgomery    OH   45424      US  US/Eastern         KFFO   
2              Hamilton    OH   45203      US  US/Eastern         KLUK   
3                Summit    OH   44311      US  US/Eastern         KAKR   
4              Hamilton    OH   45217      US  US/Eastern         KLUK   
...                 ...   ...     ...     ...         ...          ...   
2845281       Riverside    CA   92501      US  US/Pacific         KRAL   
2845282       San Diego    CA   92108      US  US/Pacific         KMYF   
2845283          Orange    CA   92866      US  US/Pacific         KSNA   
2845284     Los Angeles    CA   90230      US  US/Pacific         KSMO   
2845285  San Bernardino    CA   92346      US  US/Pacific         KSBD   

         Temperature(F)  Humidity(%)  Pressure(in)  Visibility(mi)  \
0                  42.1         58.0         29.76            10.0   
1                  36.9         91.0         29.68            10.0   
2                  36.0         97.0         29.70            10.0   
3                  39.0         55.0         29.65            10.0   
4                  37.0         93.0         29.69            10.0   
...                 ...          ...           ...             ...   
2845281            86.0         40.0         28.92            10.0   
2845282            70.0         73.0         29.39            10.0   
2845283            73.0         64.0         29.74            10.0   
2845284            71.0         81.0         29.62            10.0   
2845285            79.0         47.0         28.63             7.0   

        Wind_Direction  Wind_Speed(mph)  Precipitation(in) Weather_Condition  \
0                   SW             10.4               0.00        Light Rain   
1                 Calm              NaN               0.02        Light Rain   
2                 Calm              NaN               0.02          Overcast   
3                 Calm              NaN               0.00          Overcast   
4                  WSW             10.4               0.01        Light Rain   
...      

In [102]:
df.ident.isna().sum()

217225

In [320]:
df

ID  Severity           Start_Time  Start_Lat   Start_Lng  \
0              A-1         3  2016-02-08 00:37:08  40.108910  -83.092860   
1              A-2         2  2016-02-08 05:56:20  39.865420  -84.062800   
2              A-3         2  2016-02-08 06:15:39  39.102660  -84.524680   
3              A-4         2  2016-02-08 06:51:45  41.062130  -81.537840   
4              A-5         3  2016-02-08 07:53:43  39.172393  -84.492792   
...            ...       ...                  ...        ...         ...   
2845281  A-2845338         2  2019-08-23 18:03:25  34.002480 -117.379360   
2845282  A-2845339         2  2019-08-23 19:11:30  32.766960 -117.148060   
2845283  A-2845340         2  2019-08-23 19:00:21  33.775450 -117.847790   
2845284  A-2845341         2  2019-08-23 19:00:21  33.992460 -118.403020   
2845285  A-2845342         2  2019-08-23 18:52:06  34.133930 -117.230920   

         Distance(mi)            Street Side         City          County  \
0               3.230       Outerbelt E    R       Dublin        Franklin   
1               0.747            I-70 E    R       Dayton      Montgomery   
2               0.055            I-75 S    R   Cincinnati        Hamilton   
3               0.123            I-77 N    R        Akron          Summit   
4               0.500            I-75 S    R   Cincinnati        Hamilton   
...               ...               ...  ...          ...             ...   
2845281         0.543      Pomona Fwy E    R    Riverside       Riverside   
2845282         0.338             I-8 W    R    San Diego       San Diego   
2845283         0.561  Garden Grove Fwy    R       Orange          Orange   
2845284         0.772   San Diego Fwy S    R  Culver City     Los Angeles   
2845285         0.537          CA-210 W    R     Highland  San Bernardino   

        State Zipcode Country    Timezone Airport_Code  Temperature(F)  \
0          OH   43017      US  US/Eastern         KOSU            42.1   
1          OH   45424      US  US/Eastern         KFFO            36.9   
2          OH   45203      US  US/Eastern         KLUK            36.0   
3          OH   44311      US  US/Eastern         KAKR            39.0   
4          OH   45217      US  US/Eastern         KLUK            37.0   
...       ...     ...     ...         ...          ...             ...   
2845281    CA   92501      US  US/Pacific         KRAL            86.0   
2845282    CA   92108      US  US/Pacific         KMYF            70.0   
2845283    CA   92866      US  US/Pacific         KSNA            73.0   
2845284    CA   90230      US  US/Pacific         KSMO            71.0   
2845285    CA   92346      US  US/Pacific         KSBD            79.0   

         Humidity(%)  Pressure(in)  Visibility(mi) Wind_Direction  \
0               58.0         29.76            10.0             SW   
1               91.0         29.68            10.0           Calm   
2               97.0         29.70            10.0           Calm   
3               55.0         29.65            10.0           Calm   
4               93.0         29.69            10.0            WSW   
...              ...           ...             ...            ...   
2845281         40.0         28.92            10.0              W   
2845282         73.0         29.39            10.0             SW   
2845283         64.0         29.74            10.0            SSW   
2845284         81.0         29.62            10.0             SW   
2845285         47.0         28.63             7.0             SW   

         Wind_Speed(mph)  Precipitation(in) Weather_Condition  Amenity   Bump  \
0                   10.4               0.00        Light Rain    False  False   
1                    NaN               0.02        Light Rain    False  False   
2                    NaN               0.02          Overcast    False  False   
3                    NaN               0.00          Overcast    False  False   
4                   10.4               0.01        Ligh

# Create Final Tables

## Create Location Table

In [441]:
#Location(ID_ST : integer, State: string, City : string)
# columns to take from Accident Dataset
Location_cols = ['City', 'State']
temp = df[Location_cols]
Location = temp.copy()

# get unique values
Location.drop_duplicates(inplace = True)

# reset indices
Location.reset_index(inplace=True)
Location.drop('index', axis = 1, inplace=True)

# add ID_ST column (index)
Location.reset_index(inplace=True)
Location.rename(columns={'index':'ID_ST'}, inplace=True)


In [519]:
Location

ID_ST                          City State
0          0                        Dublin    OH
1          1                        Dayton    OH
2          2                    Cincinnati    OH
3          3                         Akron    OH
4          4                  Williamsburg    OH
...      ...                           ...   ...
16920  16920                    Bridgeboro    GA
16921  16921                       Buffalo    KS
16922  16922                      Stoneham    ME
16923  16923                    Plainfield    VT
16924  16924  American Fork-Pleasant Grove    UT

[16925 rows x 3 columns]

## Create Environment Table

In [506]:
# Environment(Env_ID : integer, Precipitation : decimal, Visibility : integer, 
#             Temperature : decimal, Humidity : decimal, weather_condition : string, 
#             Light_Or_Darkness : boolean, Air_pressure : decimal, Wind_Speed : decimal, Wind_Direction : string) 
Environment_cols = ['Precipitation(in)', 'Visibility(mi)', 'Temperature(F)', 'Humidity(%)', 'Weather_Condition',
                   'Light_Or_Darkness', 'Pressure(in)', 'Wind_Speed(mph)', 'Wind_Direction']

# create Environment table
temp = df[Environment_cols]
Environment = temp.copy()

# get unique values
Environment.drop_duplicates(inplace = True)

# reset indices
Environment.reset_index(inplace=True)
Environment.drop('index', axis = 1, inplace=True)

# # create Env_ID
Environment.reset_index(inplace=True)
Environment.rename(columns={'index':'Env_ID'}, inplace=True)



In [507]:
Environment.isna().sum()

Env_ID               0
Precipitation(in)    0
Visibility(mi)       0
Temperature(F)       0
Humidity(%)          0
Weather_Condition    0
Light_Or_Darkness    0
Pressure(in)         0
Wind_Speed(mph)      0
Wind_Direction       0
dtype: int64

In [520]:
Environment

Env_ID  Precipitation(in)  Visibility(mi)  Temperature(F)  \
0              0               0.00              10            42.1   
1              1               0.02              10            36.9   
2              2               0.02              10            36.0   
3              3               0.00              10            39.0   
4              4               0.01              10            37.0   
...          ...                ...             ...             ...   
1066050  1066050               0.00              10            93.0   
1066051  1066051               0.00               8            80.0   
1066052  1066052               0.00              10            89.0   
1066053  1066053               0.00              10            88.0   
1066054  1066054               0.00               7            79.0   

         Humidity(%) Weather_Condition Light_Or_Darkness  Pressure(in)  \
0               58.0              Rain             Night         29.76   
1               91.0              Rain             Night         29.68   
2               97.0             Clear             Night         29.70   
3               55.0             Clear             Night         29.65   
4               93.0              Rain               Day         29.69   
...              ...               ...               ...           ...   
1066050         18.0             Clear               Day         27.20   
1066051         48.0             Clear               Day         29.73   
1066052         34.0             Clear               Day         28.78   
1066053         32.0             Clear               Day         28.20   
1066054         47.0             Clear               Day         28.63   

         Wind_Speed(mph) Wind_Direction  
0                      0           Calm  
1                      0           Calm  
2                      0           Calm  
3                      0           Calm  
4                      0           Calm  
...                  ...            ...  
1066050                0           Calm  
1066051                0           Calm  
1066052                0           Calm  
1066053                0           Calm  
1066054                0           Calm  

[1066055 rows x 10 columns]

## Create Road Table

In [46]:
pd.set_option("display.max_rows", 10)

In [478]:
# Road (Street : string, Zip_Code : integer, Highway : boolean, Obstacle :  string, ID_ST: integer) 
Road_cols = ['Street', 'Zipcode', 'Amenity', 'Bump', 'Crossing', 'Give_Way', 'Junction', 'No_Exit', 
             'Railway', 'Roundabout', 'Station', 'Stop', 'Traffic_Calming', 'Traffic_Signal', 'Turning_Loop',
            'City', 'State']

# create Road table
temp = df[Road_cols]
Road = temp.copy()

# add highway boolean column to replace last column with values
# all values that would denote a highway
highway_indicators = ['-', 'Hwy', 'hwy' 'Highway', 'highway', 'Expy', 'expy', 'Expressway', 'expressway', 
                    'Fwy', 'fwy', 'Freeway', 'freeway', 'Tollway', 'tollway', 'Tlwy', 'tlwy', 
                    'Tpk', 'tpk', 'Tpke', 'tpke', 'Turnpike', 'turnpike', 'Pkwy', 'pkwy', 'Parkway', 'parkway', 
                    'State', 'state']

Road['Highway'] = 0 # instantiate column
Road.loc[Road['Street'].str.contains('|'.join(highway_indicators)) == True, 'Highway'] = 1

# create Obstacle column with obstacles that are present
Obst_cols = ['Amenity', 'Bump', 'Crossing', 'Give_Way', 'Junction', 'No_Exit', 
             'Railway', 'Roundabout', 'Station', 'Stop', 'Traffic_Calming', 'Traffic_Signal', 'Turning_Loop']
Road['Obstacle'] = 'None'

for col in Obst_cols:
    Road.loc[Road[col], 'Obstacle'] = col
    
# remove boolean obstacle columns
Road.drop(Obst_cols, axis = 1, inplace=True)

# get unique values and reset indices
Road.drop_duplicates(inplace = True)

Road.reset_index(inplace=True)
Road.drop('index', axis = 1, inplace=True)

# add ID_ST: merge with Location and get rid of City and State to get ID_ST
merge_cols = ['City', 'State']
Road = pd.merge(Road, Location, how='inner', left_on=merge_cols, right_on=merge_cols).drop(merge_cols, axis = 1)



In [518]:
Road

Street Zipcode                          City State  \
0                    Outerbelt E   43017                        Dublin    OH   
1                   Muirfield Dr   43017                        Dublin    OH   
2                       Avery Rd   43017                        Dublin    OH   
3                    Outerbelt N   43016                        Dublin    OH   
4       Columbus Marysville Rd S   43017                        Dublin    OH   
...                          ...     ...                           ...   ...   
302345          GA Highway 112 S   31705                    Bridgeboro    GA   
302346                   US-75 N   66717                       Buffalo    KS   
302347                  Maine St   04231                      Stoneham    ME   
302348                US Route 2   05667                    Plainfield    VT   
302349              N Digital Dr   84043  American Fork-Pleasant Grove    UT   

        Highway      Obstacle  ID_ST  
0             0  Turning_Loop      0  
1             0          None      0  
2             0          None      0  
3             0          None      0  
4             0          None      0  
...         ...           ...    ...  
302345        0          None  16920  
302346        1          None  16921  
302347        0          None  16922  
302348        0          None  16923  
302349        0          None  16924  

[302350 rows x 7 columns]

## Create Airport Table

In [512]:
# Airport(ICAO_ID : string, Name : string, Size : char, Latitude : decimal, Longitude : decimal, ID_ST : integer) 
Airport_cols = ['ident', 'name', 'type', 'latitude_deg', 'longitude_deg', 'municipality', 'local_region']

# create Airport table
temp = df[Airport_cols]
Airport = temp.copy()

# drop first row of metadata
# Airport.drop(index=df.index[0], axis=0, inplace=True)

# get unique values
Airport.drop_duplicates(inplace = True)

# reset indices
Airport.reset_index(inplace=True)
Airport.drop('index', axis = 1, inplace=True)

# add ID_ST: merge with Location and get rid of City and State to get ID_ST
Airport = Airport.merge(Location, left_on=['municipality','local_region'], right_on = ['City','State'], how='inner')



In [517]:
Airport

ident                                               name  \
0        KOSU  The Ohio State University Airport - Don Scott ...   
1        KCMH          John Glenn Columbus International Airport   
2        KTZR                                       Bolton Field   
3        KLCK                 Rickenbacker International Airport   
4        KFFO                    Wright-Patterson Air Force Base   
...       ...                                                ...   
3144     KOZA                            Ozona Municipal Airport   
3145     KAVK                              Alva Regional Airport   
3146     KF08                          Eufaula Municipal Airport   
3147  US-5325                                      Hatch Airport   
3148     94NH                                Tucker Farm Airport   

                type  latitude_deg  longitude_deg municipality local_region  \
0     medium_airport     40.079800     -83.072998     Columbus           OH   
1      large_airport     39.998001     -82.891899     Columbus           OH   
2      small_airport     39.901199     -83.136902     Columbus           OH   
3     medium_airport     39.813801     -82.927803     Columbus           OH   
4     medium_airport     39.826099     -84.048302       Dayton           OH   
...              ...           ...            ...          ...          ...   
3144   small_airport     30.735300    -101.203003        Ozona           TX   
3145   small_airport     36.773201     -98.669899         Alva           OK   
3146   small_airport     35.298043     -95.627378      Eufaula           OK   
3147   small_airport     37.649460    -112.418390        Hatch           UT   
3148   small_airport     43.476450     -71.747400      Andover           NH   

      ID_ST      City State  
0        10  Columbus    OH  
1        10  Columbus    OH  
2        10  Columbus    OH  
3        10  Columbus    OH  
4         1    Dayton    OH  
...     ...       ...   ...  
3144  16866     Ozona    TX  
3145  16871      Alva    OK  
3146  16880   Eufaula    OK  
3147  16913     Hatch    UT  
3148   6047   Andover    NH  

[3149 rows x 10 columns]

## Create Accident Table

### Should I split date_time into date and time, might be easier to look at stuff

In [515]:
# Accident(ID : integer, Severity : integer, Latitude : decimal, Longitude : decimal, 
#          Distance_of_traffic : decimal, Date_time : datetime, Env_ID : integer, 
#         Street : string, Zip_Code : integer, ICAO_ID : string, Distance : decimal) 
Accident_cols = ['Severity', 'Start_Lat', 'Start_Lng', 'Distance(mi)', 'Start_Time'] +  Environment_cols + ['Street', 'Zipcode'] + ['ident', 'Nearest_Air_Dist'] 

Accident = df[Accident_cols]

# get Env_ID - merge with environments to get this id
Accident = Accident.merge(Environment, left_on=Environment_cols, right_on = Environment_cols, how='inner').drop(Environment_cols, axis = 1)

# get Street and Zip_Code as foreign keys - ALREADY PART OF TABLE
# Accident = Accident.merge(Road, left_on=['Street', 'Zipcode'], right_on = ['Street', 'Zipcode'], how='inner')


In [516]:
Accident

Severity  Start_Lat   Start_Lng  Distance(mi)           Start_Time  \
0               3  40.108910  -83.092860         3.230  2016-02-08 00:37:08   
1               2  39.865420  -84.062800         0.747  2016-02-08 05:56:20   
2               2  39.102660  -84.524680         0.055  2016-02-08 06:15:39   
3               2  41.062130  -81.537840         0.123  2016-02-08 06:51:45   
4               3  39.172393  -84.492792         0.500  2016-02-08 07:53:43   
...           ...        ...         ...           ...                  ...   
2845279         2  34.629366 -118.153009         0.000  2019-08-23 15:24:47   
2845280         2  34.072330 -118.080660         0.165  2019-08-23 15:23:31   
2845281         2  34.030470 -117.598170         0.548  2019-08-23 16:26:06   
2845282         2  33.943599 -117.077880         0.000  2019-08-23 17:40:12   
2845283         2  34.133930 -117.230920         0.537  2019-08-23 18:52:06   

                        Street Zipcode ident  Nearest_Air_Dist   Env_ID  
0                  Outerbelt E   43017  KOSU          2.267484        0  
1                       I-70 E   45424  KFFO          2.820266        1  
2                       I-75 S   45203  KLUK          5.701761        2  
3                       I-77 N   44311  KAKR          4.076920        3  
4                       I-75 S   45217  KLUK          6.213225        4  
...                        ...     ...   ...               ...      ...  
2845279  Antelope Valley Fwy N   93551  KPMD          3.875102  1066050  
2845280                 I-10 W   91770  KEMT          2.785205  1066051  
2845281           Pomona Fwy E   91761  KONT          1.767090  1066052  
2845282                CA-60 E   92555  KRIV         11.274882  1066053  
2845283               CA-210 W   92346  KSBD          2.665838  1066054  

[2845284 rows x 10 columns]

In [ ]:
# change column names to column names in database
#### Location
# NOT NEEDED

#### Environment
env_rename = {'Precipitation(in)':'Precipitation' , 'Visibility(mi)' : 'Visibility', 'Temperature(F)' : 'Temperature', 
              'Humidity(%)' : 'Humidity', 'Pressure(in)' : 'Pressure', 'Wind_Speed(mph)' : 'Wind_Speed'}
Environment.rename(columns = env_rename, inplace=True)

#### Road
road_rename = {'Zipcode':'Zip_Code'}
Fin_Road.rename(columns = road_rename, inplace=True)

#### Airport
# Airport(ICAO_ID : string, Name : string, Size : char, Latitude : decimal, Longitude : decimal, ID_ST : integer) 
air_rename = {'ident' : 'ICAO_ID ', 'name' : 'Name', 'type': 'Size', 'latitude_deg' : 'Latitude', 'longitude_deg' : 'Longitude'}
Fin_Airports.rename(columns = air_rename, inplace=True)

#### Accident
acc_rename = {'Start_Lat' : 'Latitude', 'Start_Lng' : 'Longitude', 'Distance(mi)' : 'Distance_of_traffice', 
              'Start_Time' : 'Date_time', 'ident' : 'ICAO_ID'}


In [ ]:
# send to csv files
Accident.to_csv('Accident.csv', index = False)
Airport.to_csv('Airport.csv', index = False)
Road.to_csv('Road.csv', index = False)
Environment.to_csv('Environment.csv', index = False)
Location.to_csv('Location.csv', index = False)

In [ ]:
#missRanger for imputation???